## Project EDA

## Environment

In [1]:
import wandb
import pandas as pd
import pandas_profiling

## Data Import

In [2]:
run = wandb.init(project='nyc_airbnb',
                 group='eda',
                 save_code=True)
local_path = wandb.use_artifact('sample.csv:latest').file()
df = pd.read_csv(local_path)

wandb: Currently logged in as: rosaria (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.11 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


## Profile

In [3]:
profile = pandas_profiling.ProfileReport(df)
profile.to_widgets()
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/29 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

- 20K observations
- 8261 (2.6%) missing cells
- no duplicate rows
- unique IDs
- mostly distinct names (19,768 (98.9%) distinct names, 7 missing)
- some ids share same names (ID is the better measure)
- host_name: 8 missing (host_id is the better measure b/c people can share same name)
- lattitude: 12439 distinct, looks about right with no obvious outliers
- longitude: 10181 distinct, ditto
- price: how can minimum be 0 (doesn't charge anything?) and maximum be 10000? left skew 
- minimum_nights: how can maximum be 1250? 
- number of reviews: 4123 with no reviews
- last_review: date as string, 4123 with no reviews, consistent as above
- reviews_per_month: 790: left skew
- calculated_host_listings_count: 1-327 (some hosts have a large number of listings)
- availability_365: 0-365, 7176 with no availabilities? huge amount with no availabilities and some extremely available

## Data cleaning

"After talking to your stakeholders, you decide to consider from a minimum of 10 dollars to a maximum of 350 dollars per night."

In [4]:
min_price = 10
max_price = 350
idx = df['price'].between(min_price, max_price)
df = df[idx].copy()
# Convert last_review to datetime
df['last_review'] = pd.to_datetime(df['last_review'])

In [5]:
# check datetime conversion of last_review
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 19001 entries, 0 to 19999
Data columns (total 16 columns):
 #   Column                          Non-Null Count  Dtype         
---  ------                          --------------  -----         
 0   id                              19001 non-null  int64         
 1   name                            18994 non-null  object        
 2   host_id                         19001 non-null  int64         
 3   host_name                       18993 non-null  object        
 4   neighbourhood_group             19001 non-null  object        
 5   neighbourhood                   19001 non-null  object        
 6   latitude                        19001 non-null  float64       
 7   longitude                       19001 non-null  float64       
 8   room_type                       19001 non-null  object        
 9   price                           19001 non-null  int64         
 10  minimum_nights                  19001 non-null  int64         
 11  nu

In [6]:
# check price filter
df.price.describe()

count    19001.000000
mean       122.340456
std         71.530346
min         10.000000
25%         66.000000
50%        100.000000
75%        160.000000
max        350.000000
Name: price, dtype: float64

In [7]:
run.finish()